# 6 - Post-processing
## Clean-up (removing duplicates and edge detections) 📝-->🧹📝
## Converting YOLO predictions from image to map space  🧹📝--> 🗺️


## 6.1 load required libraries

In [49]:
!pip -q install geopandas
# general libraries
import os, glob
from pathlib import Path

# Geospatial libraries
import geopandas as gpd
from osgeo import gdal, osr
from shapely.geometry import Polygon


## 6.2 Get necessary files
temp_dir_predict --> path_to_predicted



tile_index_temp --> path_to_tile_index




In [ ]:
# mount google drive
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


Define a function to convert YOLO coords to utm coords

In [ ]:
##########################################################################################################################################################################
# YOLO to x1, y1, x2, y2 parsers: converts (x, y, width, height) YOLO format to (x1, y1, x2, y2)  format.
# arguments:
# - label_file: file with YOLO predictions(s) inside including: class, x, y, width, height, probabilities
# - img_width - width of input image in pixels
# - img_height - height of input image in pixels
#Returns:
# - a file with a row per predicted bounding box and the following columns: class, x1, y1, x2, y2, probability (note that the coordinates are still in image coordinates and NOT GEOGRAPHICAL ONES)

##########################################################################################################################################################################

def yolo2xy(label_file, img_width, img_height):
    """
    Definition:
Parameters:
"""
    lfile = open(label_file)
    coords = []
    all_coords = []
    for line in lfile:
        l = line.split(" ")
        label=list(map(float, list(map(float, l[0]))))
        probabs=(l[5])
        #print(probabs)
        coords = list(map(float, list(map(float, l[1:6]))))
        x1 = float(img_width) * (2.0 * float(coords[0]) - float(coords[2])) / 2.0
        y1 = float(img_height) * (2.0 * float(coords[1]) - float(coords[3])) / 2.0
        x2 = float(img_width) * (2.0 * float(coords[0]) + float(coords[2])) / 2.0
        y2 = float(img_height) * (2.0 * float(coords[1]) + float(coords[3])) / 2.0
        tmp = [int(label[0]), int(x1), int(y1), int(x2), int(y2), float(coords[4])]
        all_coords.append(list(tmp))
    lfile.close()
    return all_coords


Set input variables

In [ ]:
# Set the paths to the mosaics
my_drive_path="/content/drive/MyDrive/HOME_EXAM/data"
path_to_predicteds = [os.path.join(my_drive_path+"/tiles", folder) for folder in os.listdir(my_drive_path+"/tiles") if os.path.isdir(os.path.join(my_drive_path+"/tiles", folder))]
buffer_size_m=1


In [ ]:
path_to_predicteds

['/content/drive/MyDrive/HOME_EXAM/data/tiles/10m_krakstad_202304_sun',
 '/content/drive/MyDrive/HOME_EXAM/data/tiles/10m_ortho_hobol_042222_mavic_sun',
 '/content/drive/MyDrive/HOME_EXAM/data/tiles/10m_galbyveien_20230504_sun',
 '/content/drive/MyDrive/HOME_EXAM/data/tiles/10m_braatan_40m_20230605_sun']

In [ ]:
annotator_ID=20 # change this to your folder ID


# Run a loop for each area

In [ ]:
# path_to_predicteds = [path_to_predicteds[0], path_to_predicteds[1], path_to_predicteds[3]] #Remove Braatan mosaic


In [ ]:
for path_to_predicted in path_to_predicteds:
  basename = os.path.basename(path_to_predicted)
  basename = basename.replace("10m_", "")
  path_to_tile_index = path_to_predicted+"/"+basename+"_tile_index.shp"

  # get list of images (.tif) and labels (.txt)
  gtiffs = glob.glob(path_to_predicted + "/*.tif")
  labels = glob.glob(path_to_predicted + "/predict_tile_20/labels/*.txt")
  print("There a total of "+str(len(gtiffs))+" tif files")
  print("There a total of "+str(len(labels))+" label files")

  # load tile index
  tile_index = gpd.read_file(path_to_tile_index)

  # Get raster metadata
  # pixel resolution (in meters) and tile size in pixels
  src_ds = gdal.Open(gtiffs[0]) # get raster datasource
  _, xres, _, _, _, yres  = src_ds.GetGeoTransform() # get pixel size in meters
  tile_size_m=round(src_ds.RasterXSize*xres)
  tile_size_px= round(tile_size_m/abs(xres)) # calculate the tile size in pixels
  ## Get EPSG code
  proj = osr.SpatialReference(wkt=src_ds.GetProjection())
  EPSG_code= proj.GetAttrValue('AUTHORITY',1)

  print("Resolution: "+str(round(xres,2))+" m")
  print("EPSG: "+str(EPSG_code))

  # Get raster metadata
  # pixel resolution (in meters) and tile size in pixels
  src_ds = gdal.Open(gtiffs[0]) # get raster datasource
  _, xres, _, _, _, yres  = src_ds.GetGeoTransform() # get pixel size in meters
  tile_size_m=round(src_ds.RasterXSize*xres)
  tile_size_px= round(tile_size_m/abs(xres)) # calculate the tile size in pixels
  ## Get EPSG code
  proj = osr.SpatialReference(wkt=src_ds.GetProjection())
  EPSG_code= proj.GetAttrValue('AUTHORITY',1)

  print("Resolution: "+str(round(xres,2))+" m")
  print("EPSG: "+str(EPSG_code))

  ##########################################################################################################################################################################
  # YOLO to x1, y1, x2, y2 parsers: converts (x, y, width, height) YOLO format to (x1, y1, x2, y2)  format.
  # arguments:
  # - label_file: file with YOLO predictions(s) inside including: class, x, y, width, height, probabilities
  # - img_width - width of input image in pixels
  # - img_height - height of input image in pixels
  #Returns:
  # - a file with a row per predicted bounding box and the following columns: class, x1, y1, x2, y2, probability (note that the coordinates are still in image coordinates and NOT GEOGRAPHICAL ONES)

  ##########################################################################################################################################################################

  def yolo2xy(label_file, img_width, img_height):
      """
      Definition:
  Parameters:
  """
      lfile = open(label_file)
      coords = []
      all_coords = []
      for line in lfile:
          l = line.split(" ")
          label=list(map(float, list(map(float, l[0]))))
          probabs=(l[5])
          #print(probabs)
          coords = list(map(float, list(map(float, l[1:6]))))
          x1 = float(img_width) * (2.0 * float(coords[0]) - float(coords[2])) / 2.0
          y1 = float(img_height) * (2.0 * float(coords[1]) - float(coords[3])) / 2.0
          x2 = float(img_width) * (2.0 * float(coords[0]) + float(coords[2])) / 2.0
          y2 = float(img_height) * (2.0 * float(coords[1]) + float(coords[3])) / 2.0
          tmp = [int(label[0]), int(x1), int(y1), int(x2), int(y2), float(coords[4])]
          all_coords.append(list(tmp))
      lfile.close()
      return all_coords

  all_bboxes = None
  iter_all=0 # setup counter
  for lab in range(len(labels)):
      print(str(round(lab/len(labels)*100))+" % done!", end="\r")
      # Define one label file and select the corresponding geotiff image
      label_file=labels[lab]
      label_file_name=Path(label_file).stem # ortho name
      for p in gtiffs:
          if Path(p).stem ==label_file_name:
              gtiff_file=p

      # determing image witdth and height
      try:
        r = gdal.Open(gtiff_file)
      except:
        print("no file")
        continue

      img_width=r.RasterXSize
      img_height=r.RasterYSize

      # Convert from yolo coordinates to x1, y1, x2, y2,
      coords = yolo2xy(label_file, img_width, img_height) # class, x1, y1, x2, y2, probability

      # Convert from image to geographical coordinates
      ## select tile polygon (from tile index shapefile) that corresponds to the label_file_name
      # the other files are required by the gpd readfile


      # tile_index is <class 'geopandas.geodataframe.GeoDataFrame'>
      one_tile=tile_index[tile_index['ID']==label_file_name+".tif"] # Select tile in tile_index that has ID equal to label_file_name

      ## get tile bounding box geographical coordinates (UTM)
      one_tile_XminUTM=one_tile.total_bounds[0]
      one_tile_YminUTM=one_tile.total_bounds[1]
      one_tile_XmaxUTM=one_tile.total_bounds[2]
      one_tile_YmaxUTM=one_tile.total_bounds[3]

      ## take inner buffer equal to the buffer_size_m
      one_tile_innerB= one_tile
      one_tile_innerB['geometry'] = one_tile_innerB.geometry.buffer(-(buffer_size_m/2))

      ## get inner tile bounding boxes
      one_tile_inner_XminUTM=one_tile_innerB.total_bounds[0]
      one_tile_inner_YminUTM=one_tile_innerB.total_bounds[1]
      one_tile_inner_XmaxUTM=one_tile_innerB.total_bounds[2]
      one_tile_inner_YmaxUTM=one_tile_innerB.total_bounds[3]

      # Now iterate through each bounding box and assign UTM coordinates and create a shapefile
      bboxes_tile = None
      for i in coords:
          # print("inside coords")
          # Convert bounding box coordinates from image to geographical coords
          X1_UTM=(i[1]*xres)+one_tile_XminUTM
          Y1_UTM=(i[2]*yres)+one_tile_YminUTM+tile_size_m
          X2_UTM=(i[3]*xres)+one_tile_XminUTM
          Y2_UTM=(i[4]*yres)+one_tile_YminUTM+tile_size_m

          # skip bounding box if its centroid is NOT within the inner tile (removing the overlap)
          X_UTM= (X1_UTM+X2_UTM)/2
          Y_UTM= (Y1_UTM+Y2_UTM)/2
          if X_UTM<one_tile_inner_XminUTM or X_UTM>one_tile_inner_XmaxUTM or Y_UTM<one_tile_inner_YminUTM or Y_UTM>one_tile_inner_YmaxUTM:
              #print("continue break")
              continue


          # Create polygon shape from geographical coords
          lat_point_list = [Y1_UTM, Y1_UTM, Y2_UTM, Y2_UTM, Y1_UTM]
          lon_point_list = [X1_UTM, X2_UTM, X2_UTM, X1_UTM, X1_UTM]
          try:
            polygon_geom = Polygon(zip(lon_point_list, lat_point_list))
          except:
            print("not sure what is going on")
            continue

          crs = {'init': 'epsg:'+EPSG_code}
          data= {'class': [i[0]], 'prob': [i[5]]}
          bbox = gpd.GeoDataFrame(data, crs=crs, geometry=[polygon_geom])

          if (bboxes_tile is None):
              bboxes_tile = bbox
          else:
              bboxes_tile = bboxes_tile.append(bbox)

      # cleanup boxes (removing overlapping ones)
      if bboxes_tile is not None:
          #clean_boxes = bboxes_tile #cleanUp_boudingBoxes(bboxes_tile, iou_thresh)
          if (all_bboxes is None):
              all_bboxes = bboxes_tile
          else :
              all_bboxes = all_bboxes.append(bboxes_tile)

  print("Export to shp")
  ortho_name= os.path.basename(path_to_predicted)
  print(all_bboxes)
  print(path_to_predicted + "/" + ortho_name + "_predictions_"+str(annotator_ID)+".shp")
  all_bboxes.to_file(path_to_predicted + "/" + ortho_name + "_predictions_"+str(annotator_ID)+".shp", driver='ESRI Shapefile') # turn this off if it's not needed


There a total of 217 tif files
There a total of 209 label files
Resolution: 0.01 m
EPSG: 25832
Resolution: 0.01 m
EPSG: 25832


/usr/local/lib/python3.10/dist-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/usr/local/lib/python3.10/dist-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

<ipython-input-61-65c9a476dac8>:165: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_bboxes = all_bboxes.append(bboxes_tile)
/usr/local/lib/python3.10/dist-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/us

/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
<ipython-input-61-65c9a476dac8>:157: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  bboxes_tile = bboxes_tile.append(bbox)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
<ipython-input-

/usr/local/lib/python3.10/dist-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mind

...

/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
<ipython-input-61-65c9a476dac8>:157: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  bboxes_tile = bboxes_tile.append(bbox)
/usr/local/lib/

not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on
not sure what is going on


<ipython-input-61-65c9a476dac8>:165: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  all_bboxes = all_bboxes.append(bboxes_tile)
/usr/local/lib/python3.10/dist-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
<ip

Export to shp
    class      prob                                           geometry
0       0  0.172595  POLYGON ((610866.504 6622679.964, 610866.793 6...
0       0  0.208500  POLYGON ((610882.687 6622677.006, 610882.968 6...
0       0  0.332000  POLYGON ((610893.431 6622683.049, 610894.077 6...
0       0  0.200282  POLYGON ((610887.906 6622680.915, 610888.067 6...
0       0  0.195113  POLYGON ((610893.992 6622683.720, 610894.213 6...
..    ...       ...                                                ...
0       0  0.287488  POLYGON ((611089.174 6622461.824, 611089.438 6...
0       0  0.711054  POLYGON ((611101.856 6622457.693, 611102.094 6...
0       0  0.467282  POLYGON ((611084.279 6622452.976, 611084.534 6...
0       0  0.543814  POLYGON ((611089.769 6622450.111, 611089.990 6...
0       0  0.509194  POLYGON ((611093.968 6622454.327, 611094.189 6...

[797 rows x 3 columns]
/content/drive/MyDrive/HOME_EXAM/data/tiles/10m_braatan_40m_20230605_sun/10m_braatan_40m_20230605_sun_predicti

/usr/local/lib/python3.10/dist-packages/geopandas/geodataframe.py:1538: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mind

Now for the full_data

In [ ]:
# set paths
annotator_ID="full_data" #


In [ ]:
for path_to_predicted in path_to_predicteds:
  basename = os.path.basename(path_to_predicted)
  basename = basename.replace("10m_", "")
  path_to_tile_index = path_to_predicted+"/"+basename+"_tile_index.shp"

  # get list of images (.tif) and labels (.txt)
  gtiffs = glob.glob(path_to_predicted + "/*.tif")
  labels = glob.glob(path_to_predicted + "/predict_tile_"+annotator_ID+"/labels/*.txt")
  print("There a total of "+str(len(gtiffs))+" tif files")
  print("There a total of "+str(len(labels))+" label files")

  # load tile index
  tile_index = gpd.read_file(path_to_tile_index)

  # Get raster metadata
  # pixel resolution (in meters) and tile size in pixels
  src_ds = gdal.Open(gtiffs[0]) # get raster datasource
  _, xres, _, _, _, yres  = src_ds.GetGeoTransform() # get pixel size in meters
  tile_size_m=round(src_ds.RasterXSize*xres)
  tile_size_px= round(tile_size_m/abs(xres)) # calculate the tile size in pixels
  ## Get EPSG code
  proj = osr.SpatialReference(wkt=src_ds.GetProjection())
  EPSG_code= proj.GetAttrValue('AUTHORITY',1)

  print("Resolution: "+str(round(xres,2))+" m")
  print("EPSG: "+str(EPSG_code))

  # Get raster metadata
  # pixel resolution (in meters) and tile size in pixels
  src_ds = gdal.Open(gtiffs[0]) # get raster datasource
  _, xres, _, _, _, yres  = src_ds.GetGeoTransform() # get pixel size in meters
  tile_size_m=round(src_ds.RasterXSize*xres)
  tile_size_px= round(tile_size_m/abs(xres)) # calculate the tile size in pixels
  ## Get EPSG code
  proj = osr.SpatialReference(wkt=src_ds.GetProjection())
  EPSG_code= proj.GetAttrValue('AUTHORITY',1)

  print("Resolution: "+str(round(xres,2))+" m")
  print("EPSG: "+str(EPSG_code))

  ##########################################################################################################################################################################
  # YOLO to x1, y1, x2, y2 parsers: converts (x, y, width, height) YOLO format to (x1, y1, x2, y2)  format.
  # arguments:
  # - label_file: file with YOLO predictions(s) inside including: class, x, y, width, height, probabilities
  # - img_width - width of input image in pixels
  # - img_height - height of input image in pixels
  #Returns:
  # - a file with a row per predicted bounding box and the following columns: class, x1, y1, x2, y2, probability (note that the coordinates are still in image coordinates and NOT GEOGRAPHICAL ONES)

  ##########################################################################################################################################################################

  def yolo2xy(label_file, img_width, img_height):
      """
      Definition:
  Parameters:
  """
      lfile = open(label_file)
      coords = []
      all_coords = []
      for line in lfile:
          l = line.split(" ")
          label=list(map(float, list(map(float, l[0]))))
          probabs=(l[5])
          #print(probabs)
          coords = list(map(float, list(map(float, l[1:6]))))
          x1 = float(img_width) * (2.0 * float(coords[0]) - float(coords[2])) / 2.0
          y1 = float(img_height) * (2.0 * float(coords[1]) - float(coords[3])) / 2.0
          x2 = float(img_width) * (2.0 * float(coords[0]) + float(coords[2])) / 2.0
          y2 = float(img_height) * (2.0 * float(coords[1]) + float(coords[3])) / 2.0
          tmp = [int(label[0]), int(x1), int(y1), int(x2), int(y2), float(coords[4])]
          all_coords.append(list(tmp))
      lfile.close()
      return all_coords

  all_bboxes = None
  iter_all=0 # setup counter
  for lab in range(len(labels)):
      print(str(round(lab/len(labels)*100))+" % done!", end="\r")
      # Define one label file and select the corresponding geotiff image
      label_file=labels[lab]
      label_file_name=Path(label_file).stem # ortho name
      for p in gtiffs:
          if Path(p).stem ==label_file_name:
              gtiff_file=p

      # determing image witdth and height
      try:
        r = gdal.Open(gtiff_file)
      except:
        print("no file")
        continue

      img_width=r.RasterXSize
      img_height=r.RasterYSize

      # Convert from yolo coordinates to x1, y1, x2, y2,
      coords = yolo2xy(label_file, img_width, img_height) # class, x1, y1, x2, y2, probability

      # Convert from image to geographical coordinates
      ## select tile polygon (from tile index shapefile) that corresponds to the label_file_name
      # the other files are required by the gpd readfile


      # tile_index is <class 'geopandas.geodataframe.GeoDataFrame'>
      one_tile=tile_index[tile_index['ID']==label_file_name+".tif"] # Select tile in tile_index that has ID equal to label_file_name

      ## get tile bounding box geographical coordinates (UTM)
      one_tile_XminUTM=one_tile.total_bounds[0]
      one_tile_YminUTM=one_tile.total_bounds[1]
      one_tile_XmaxUTM=one_tile.total_bounds[2]
      one_tile_YmaxUTM=one_tile.total_bounds[3]

      ## take inner buffer equal to the buffer_size_m
      one_tile_innerB= one_tile
      one_tile_innerB['geometry'] = one_tile_innerB.geometry.buffer(-(buffer_size_m/2))

      ## get inner tile bounding boxes
      one_tile_inner_XminUTM=one_tile_innerB.total_bounds[0]
      one_tile_inner_YminUTM=one_tile_innerB.total_bounds[1]
      one_tile_inner_XmaxUTM=one_tile_innerB.total_bounds[2]
      one_tile_inner_YmaxUTM=one_tile_innerB.total_bounds[3]

      # Now iterate through each bounding box and assign UTM coordinates and create a shapefile
      bboxes_tile = None
      for i in coords:
          # print("inside coords")
          # Convert bounding box coordinates from image to geographical coords
          X1_UTM=(i[1]*xres)+one_tile_XminUTM
          Y1_UTM=(i[2]*yres)+one_tile_YminUTM+tile_size_m
          X2_UTM=(i[3]*xres)+one_tile_XminUTM
          Y2_UTM=(i[4]*yres)+one_tile_YminUTM+tile_size_m

          # skip bounding box if its centroid is NOT within the inner tile (removing the overlap)
          X_UTM= (X1_UTM+X2_UTM)/2
          Y_UTM= (Y1_UTM+Y2_UTM)/2
          if X_UTM<one_tile_inner_XminUTM or X_UTM>one_tile_inner_XmaxUTM or Y_UTM<one_tile_inner_YminUTM or Y_UTM>one_tile_inner_YmaxUTM:
              #print("continue break")
              continue


          # Create polygon shape from geographical coords
          lat_point_list = [Y1_UTM, Y1_UTM, Y2_UTM, Y2_UTM, Y1_UTM]
          lon_point_list = [X1_UTM, X2_UTM, X2_UTM, X1_UTM, X1_UTM]
          try:
            polygon_geom = Polygon(zip(lon_point_list, lat_point_list))
          except:
            print("not sure what is going on")
            continue

          crs = {'init': 'epsg:'+EPSG_code}
          data= {'class': [i[0]], 'prob': [i[5]]}
          bbox = gpd.GeoDataFrame(data, crs=crs, geometry=[polygon_geom])

          if (bboxes_tile is None):
              bboxes_tile = bbox
          else:
              bboxes_tile = bboxes_tile.append(bbox)

      # cleanup boxes (removing overlapping ones)
      if bboxes_tile is not None:
          #clean_boxes = bboxes_tile #cleanUp_boudingBoxes(bboxes_tile, iou_thresh)
          if (all_bboxes is None):
              all_bboxes = bboxes_tile
          else :
              all_bboxes = all_bboxes.append(bboxes_tile)

  print("Export to shp")
  ortho_name= os.path.basename(path_to_predicted)
  print(all_bboxes)
  print(path_to_predicted + "/" + ortho_name + "_predictions_"+str(annotator_ID)+".shp")
  all_bboxes.to_file(path_to_predicted + "/" + ortho_name + "_predictions_"+str(annotator_ID)+".shp", driver='ESRI Shapefile') # turn this off if it's not needed


Output hidden; open in https://colab.research.google.com to view.

In [ ]:

#for path_to_predicted in path_to_predicteds:
for path_to_predicted in path_to_predicteds:
  print()
  print(path_to_predicted)
  basename = os.path.basename(path_to_predicted)
  basename = basename.replace("10m_", "")
  path_to_tile_index = path_to_predicted+"/"+basename+"_tile_index.shp"

  # get list of images (.tif) and labels (.txt)
  gtiffs = glob.glob(path_to_predicted + "/*.tif")
  labels = glob.glob(path_to_predicted + "/predict_tile_"+str(annotator_ID)+"/labels/*.txt") ## here is have to be changed for the full data for "predit_tiles_20"
  print("There a total of "+str(len(gtiffs))+" .tif files")
  print("There a total of "+str(len(labels))+" .label files")

  # load tile index
  tile_index = gpd.read_file(path_to_tile_index)

  # Get raster metadata
  # pixel resolution (in meters) and tile size in pixels
  src_ds = gdal.Open(gtiffs[0]) # get raster datasource
  _, xres, _, _, _, yres  = src_ds.GetGeoTransform() # get pixel size in meters
  tile_size_m=round(src_ds.RasterXSize*xres)
  tile_size_px= round(tile_size_m/abs(xres)) # calculate the tile size in pixels
  ## Get EPSG code
  proj = osr.SpatialReference(wkt=src_ds.GetProjection())
  EPSG_code= proj.GetAttrValue('AUTHORITY',1)

  print("Resolution: "+str(round(xres,2))+" m")
  print("EPSG: "+str(EPSG_code))

  ##########
  ##
  ## Parse from YOLO (image space) to UTM coordinates (map space)
  ##
  #########
  print()
  print("Parse from YOLO (image space) to UTM coordinates (map space)")
  all_bboxes = None
  iter_all=0 # setup counter
  for lab in range(len(labels)):
      print()
      print(labels[lab])
      print()
      print(str(round(lab/len(labels)*100))+" % done!", end="\r")
      # Define one label file and select the corresponding geotiff image
      label_file=labels[lab]
      label_file_name=Path(label_file).stem # ortho name
      for p in gtiffs:
          if Path(p).stem ==label_file_name:
              gtiff_file=p

      #print("debug label file = " + label_file)
      #print("debug tif file = " + gtiff_file)

      # determing image witdth and height
      r = gdal.Open(gtiff_file)
      img_width=r.RasterXSize
      img_height=r.RasterYSize

      # Convert from yolo coordinates to x1, y1, x2, y2,
      coords = yolo2xy(label_file, img_width, img_height) # class, x1, y1, x2, y2, probability

      # Convert from image to geographical coordinates
      ## select tile polygon (from tile index shapefile) that corresponds to the label_file_name
      # the other files are required by the gpd readfile


      # tile_index is <class 'geopandas.geodataframe.GeoDataFrame'>
      one_tile=tile_index[tile_index['ID']==label_file_name+".tif"] # Select tile in tile_index that has ID equal to label_file_name

      ## get tile bounding box geographical coordinates (UTM)
      one_tile_XminUTM=one_tile.total_bounds[0]
      one_tile_YminUTM=one_tile.total_bounds[1]
      one_tile_XmaxUTM=one_tile.total_bounds[2]
      one_tile_YmaxUTM=one_tile.total_bounds[3]

      ## take inner buffer equal to the buffer_size_m
      one_tile_innerB= one_tile
      one_tile_innerB['geometry'] = one_tile_innerB.geometry.buffer(-(buffer_size_m/2))

      ## get inner tile bounding boxes
      one_tile_inner_XminUTM=one_tile_innerB.total_bounds[0]
      one_tile_inner_YminUTM=one_tile_innerB.total_bounds[1]
      one_tile_inner_XmaxUTM=one_tile_innerB.total_bounds[2]
      one_tile_inner_YmaxUTM=one_tile_innerB.total_bounds[3]

      # Now iterate through each bounding box and assign UTM coordinates and create a shapefile
      bboxes_tile = None
      for i in coords:
          # print("inside coords")
          # Convert bounding box coordinates from image to geographical coords
          X1_UTM=(i[1]*xres)+one_tile_XminUTM
          Y1_UTM=(i[2]*yres)+one_tile_YminUTM+tile_size_m
          X2_UTM=(i[3]*xres)+one_tile_XminUTM
          Y2_UTM=(i[4]*yres)+one_tile_YminUTM+tile_size_m

          # skip bounding box if its centroid is NOT within the inner tile (removing the overlap)
          X_UTM= (X1_UTM+X2_UTM)/2
          Y_UTM= (Y1_UTM+Y2_UTM)/2
          if X_UTM<one_tile_inner_XminUTM or X_UTM>one_tile_inner_XmaxUTM or Y_UTM<one_tile_inner_YminUTM or Y_UTM>one_tile_inner_YmaxUTM:
              #print("continue break")
              continue


          # Create polygon shape from geographical coords
          lat_point_list = [Y1_UTM, Y1_UTM, Y2_UTM, Y2_UTM, Y1_UTM]
          lon_point_list = [X1_UTM, X2_UTM, X2_UTM, X1_UTM, X1_UTM]
          polygon_geom = Polygon(zip(lon_point_list, lat_point_list))
          crs = {'init': 'epsg:'+EPSG_code}
          data= {'class': [i[0]], 'prob': [i[5]]}
          bbox = gpd.GeoDataFrame(data, crs=crs, geometry=[polygon_geom])

          if (bboxes_tile is None):
              bboxes_tile = bbox
          else:
              bboxes_tile = bboxes_tile.append(bbox)

      # cleanup boxes (removing overlapping ones)
      if bboxes_tile is not None:
          #clean_boxes = bboxes_tile #cleanUp_boudingBoxes(bboxes_tile, iou_thresh)
          if (all_bboxes is None):
              all_bboxes = bboxes_tile
          else :
              all_bboxes = all_bboxes.append(bboxes_tile)
  print(all_bboxes)

#######
##
## Export predictions shapefile
#########
  print()
  print("Export to shp")
  ortho_name= os.path.basename(path_to_predicted)
  print(all_bboxes)
  print(path_to_predicted + "/" + ortho_name + "_predictions_"+str(annotator_ID)+".shp")
  all_bboxes.to_file(path_to_predicted + "/" + ortho_name + "_predictions_"+str(annotator_ID)+".shp", driver='ESRI Shapefile') # turn this off if it's not needed



Output hidden; open in https://colab.research.google.com to view.